# Data Analysis in pandas Courselet

**Author:** David Koop (dakoop@niu.edu)

**Last Updated:** 2025-09-19

This courselet provides background information on using the pandas library in python. It focuses on operations designed to wrangle data but includes a number of details on using pandas to load, structure, and query data. There are exercises throughout as well as a challenging final part to test your skills. We will use the City of Chicago's [Food Inspection Data](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5) for this courselet.

This first cell loads a specific subset of data from the food inspection data.

In [ ]:
%config InteractiveShell.ast_node_interactivity = 'last_expr_or_assign'

In [ ]:
import urllib.request
import gzip

url = "https://data.cityofchicago.org/resource/4ijn-s7e5.csv?"
params = {
    "$where": "2000000 <= inspection_id AND inspection_id <= 2500000",
    "$limit": "100000",
}
encoded_params = urllib.parse.urlencode(params)
# print(url + encoded_params)
request = urllib.request.Request(url + encoded_params)
request.add_header("accept-encoding", "gzip")
with urllib.request.urlopen(request) as response:
    if response.info().get("Content-Encoding") == "gzip":
        with open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())
    else:
        with gzip.open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())

### Reading Data

pandas has a number of methods to read in data, supporting a variety of different formats. Some of them, like `read_xlsx`, which reads Office spreadsheets, require external libraries to be installed. Others are written specifically for pandas. Some popular formats include:

  * **csv:** Comma-Separated Values. This is a text-based format where attributes are separated by commas. When values themselves have commas, double-quotes are used to delineate the beginning and ending of the value. Because this is a text-based format, there is no type information provided. pandas will try to *infer* the types when possible, but users may need to specify these types to help in some cases.
  * **parquet:** Apache Parquet. A standard binary format that stores values by row groups and columns. It can compress values and store type information. This requires the `pyarrow` package to be installed.
  * **json:** JavaScript Object Notation. A textual format that mimics the specification of nested objects and lists in JavaScript, but limits values to literals. While it does not store type information, it can be paired with a schema and some information can be inferred from the representation (numeric values are specified without strings, for example)

pandas can read some compressed formats, including gzipped csv files, without the need to first decompress them.

First, we need to import the pandas library. There is a convention to abbreviate pandas ad `pd`, and we will use this convention in this notebook. We can read the Chicago Food Inspections data directly using the `read_csv` method and its support for gzipped files.

In [ ]:
import pandas as pd

df = pd.read_csv("Food_Inspections.csv.gz")

The output, called a **data frame**, looks like a sheet from a spreadsheet program or perhaps a table. It shows a bold header row show the *label* for the column. On the left-hand side, the dataframe has an unnamed column that is the **index** that currently looks like an array index (more on this later). Then, a subset of values are listed; by default, these are the first and last five rows from the dataframe. Finally, the shape (number of rows and columns) of the dataframe is shown.

You can extract a single column from the data frame using brackets: `df['dba_name']` In some cases, you can also use dot notation, but this is less reliable because the column name must be a valid identifier.

In [ ]:
df["results"]

##### Exercise

You can project multiple columns at once by passing a list to the subscript operator. Try extracting both the `DBA Name` column and the `results` column. Note that this will look different than the single column extracted above. A single column returns a *Series* while multiple columns returns a *Data Frame*.

In [ ]:
# Your code here

##### Solution

In [ ]:
df[["dba_name", "results"]]

### Extracting data items

To extract a data item, you can use either the `.loc` or `.iloc` accessors. `.loc` locates items by the index **label** while `.iloc` functions uses the **position** as an integer. Note that you can access a row using bracket notation and passing in the corresponding index label (or sometimes integer position), but the ambiguity in what the code does is problematic and will be removed in future versions of pandas. When you extract a single item, you will again see a *Series* but this time it will be composed of mixed types. Pandas treats rows and columns in a similar manner, and you can even *transpose* a data frame to switch between representations.

In [ ]:
df.loc[0]

In [ ]:
df.iloc[0]

When you extract a slice of a data frame, a dataframe is returned, even if that slice only contains one item. You can slice with both `.loc` and `.iloc`. While `.iloc` returns a slice that goes up to but not including the right-most index, `.loc` returns an returns a right-*inclusive* slice! (Note that slicing in `.loc` doesn't make much sense in some cases but may be useful for a datetime index.)

In [ ]:
df.iloc[:1]

In [ ]:
df.loc[:1]

You can also examine just the beginning and end of a dataframe using the `head` and `tail` methods, which take an optional argument for the number of rows to show.

In [ ]:
df.head()

In [ ]:
df.tail(3)

### Inspecting Dataframes

In the notebook, we can see the column names for a dataframe in the output, but we can also access these columns directly via the `columns` attribute. We can also see more information about the dataframe, including the column types and non-null counts using the `info` method.

In [ ]:
df.columns

In [ ]:
df.info()

Like numpy arrays and relational databases, pandas keeps a data *type* (or `dtype`) for each column. For numeric types, we have float and int variants using different numbers of bits (e.g. `int64` or `float64`), but pandas also supports datetime, string and categorical types. The string representation of a Series usually lists its dtype, but you can retrieve it directly (`s.dtype`).

In [ ]:
df["longitude"].dtype

The number of object dtypes here generally means that these columns are populated with strings, but could also indicate mixed types.

In [ ]:
s = pd.Series(["a", 12, 34.5])
s.dtype, [type(d) for d in s]

### Dataframe Overview

While the standard dataframe output is often good enough to undersand the contents of the dataframe and see example values, and `info()` provides a horizontally-oriented overview, `describe` provides statistics about the values of the columns.

In [ ]:
df.describe()

*Note:* There are only five columns listed here, not the 16 we expect! `describe` works best with numeric data and so it only only shows the columns that are numeric for the given statistics. You can change this behavior by using the `include='all'` setting to show all columns. 

In [ ]:
df.describe(include="all")

Here, some of the properites are not relevant for non-numeric columns and those are set to `NaN`.

### Modifying the Schema

In addition, we can choose to rename columns using a `rename` method that returns an updated data frame.

In [ ]:
df = df.rename(columns={"license_": "license"})

We can also convert between types when appropriate using the `astype` method. For a Series, it requires just the type, but for a DataFrame, we pass a dictionary with the column-dtype pairs.

##### Exercise

We would like the zip code (`zip`) and license (now renamed from `license_` to `license`) columns to store integers. Try changing them to an int type. Your code will probably not work--that's ok. Why do you think this happens?

In [ ]:
### Your code here

##### Solution

In [ ]:
### !!! this code will not work !!!
df.astype({"license": "int64", "zip": "int64"})

#### Nullable Types

You should have noticed that a straightforward casting did not work. The reason is that some of the entries did not specify the license or zip code. That is also the reason these fields were intially set as float64 because the `NaN` value is used to identify missing values; int64 has no such value. We could employ an unused value (like -9999) to represent a missing value, but this might differ from dataset to dataset. pandas provides nullable types (e.g. `Int64`) that add support for null values. (Note that in newer versions of pandas, you can also specify a `dtype_backend` to switch between a numpy-backed column and the pyarrow version.) Try converting the two columns to the `Int64` type. 

##### Exercise

In [ ]:
# Your code here

##### Solution

In [ ]:
df = df.astype({"license": "Int64", "zip": "Int64"})

### Timestamps

pandas also supports datetime values. There are a number of formats for dates and times, and pandas offers a number of ways to steer the `to_datetime` utility function to obtain the correct date. Often, calling this method without parameters works well. In addition, the `read_csv` method has a `parse_dates` parameter to allow it to parse dates as it reads in the data.

In [ ]:
pd.to_datetime(df.inspection_date)

### Updating Dataframes

To keep this data, we have a few options in pandas. One way is to use the bracket syntax (`df['inspection_date'] = pd.to_datetime(df.inspection_date)`). This works here, but modifies the dataframe in place. In some cases, these operations can also produce the `SettingWithCopyWarning`. The `assign` method returns a new dataframe and never runs into this issue.

In [ ]:
df.assign(inspection_date=pd.to_datetime(df.inspection_date))

A slightly better version is to use the lambda function here so that the assign works regardless of the name of the dataframe.

In [ ]:
df = df.assign(inspection_date=lambda df: pd.to_datetime(df.inspection_date))

### Derived Data

In addition to converting columns, we can also create new columns from existing columns via operations. For example, we might wish to construct an `full_address` column that combines the `address`, `city`, `state`, and `zip` columns. In this case, `+` functions as concatenation. For numeric columns, we could use other arithmetic operators to compute derived columns.

In [ ]:
df.assign(
    full_address=df.address
    + "\n"
    + df.city
    + ", "
    + df.state
    + " "
    + df.zip.astype(str)
)

### Queries

With some initial processing completed, we can begin our analysis of the data. We have already seen how pandas allows us to select rows using labels in the `loc` accessor (`df.loc[43]`), but we can also use this accessor to filter our dataframe to those values that match particular criteria. For example, if we want to find all the inspections that were given a pass, we could do that with the boolean expression `df.results == 'Pass'`. This works because the boolean operations are applied to every item in the series, resulting in a new boolean series. That sequence of True and False values is used to pull out the correct rows. Note that here, `.loc` is often omitted as the query works without it.

In [ ]:
df.loc[df.results == "Pass"]

In [ ]:
df[df.results == "Pass"]

An alternative approach is the `query` method which takes the query as a string and parses it and executes the query. It has some advantages including no need to prefix the column names with the dataframe variable, and a smarter order of operations for the and (&) and or(|) operators. However, code completion won't work and errors can sometimes be more difficult to parse.

In [ ]:
df.query('results == "Pass"')

### Boolean Comparators & Operators

Suppose we are interested in all the inspections that received a pass in the 60608 zip code. Python's normal comparators (`>`, `<`, `>=`, `<=`, `==`, `!=`) can be used directly in column expressions. However, the operators `and`, `or`, and `not` will not work.

In [ ]:
df[df["results"] == "Pass" and df["zip"] == 60608]

This is a somewhat cryptic error, but the issue is that the `and` operator is not allowed. We must use the bitwise operators instead `&` (and), `|` (or), and `~` (not).

In [ ]:
df[df["results"] == "Pass" & df["zip"] == 60608]

This error is even more cryptic, but the reason here is that we ensure the boolean comparisons happen first which requires parentheses.

In [ ]:
df[(df["results"] == "Pass") & (df["zip"] == 60608)]

If you use the `query` method, you don't have to worry about the parentheses because pandas redefines the order of operations for the bitwise operations. You can also use the `and`, `or`, or `not` operators instead of their bitwise versions.

In [ ]:
df.query('results == "Pass" and zip == 60608')

##### Exercise

Find all inspections that received a `"Pass"` or `"Pass w/ Conditions"` and were not "Restaurant" facilities.

In [ ]:
# Your code here

##### Solution



In [ ]:
df[
    ((df["results"] == "Pass") | (df["results"] == "Pass w/ Conditions"))
    & ~(df["facility_type"] == "Restaurant")
]

In [ ]:
df.query(
    '((results == "Pass") | (results == "Pass w/ Conditions")) & (facility_type != "Restaurant")'
)

### Indexing

Up until now, we have largely ignored the leftmost column of the dataframe. pandas keeps an **index** for every dataframe and series. In our case, that index looked like an integer row index starting with 0. However, there is no restriction that index values are in order or are numeric. We could create a series that has an index of state abbreviations and values with the associated state names. In this case, the series looks like an associative array, and it works like one. We can even pass a dictionary (of key-value pairs) to the `Series` constructor.

In [ ]:
states = pd.Series(
    {"IL": "Illinois", "IN": "Indiana", "WI": "Wisconsin", "MI": "Michigan"}
)

In [ ]:
states["IL"]

But the index can do more. Suppose we have a second series of capitals for the states. We can concatenate them to create the fully-qualified capital city name, but importantly, we don't have to worry about the positions.

In [ ]:
capitals = pd.Series(
    {"WI": "Madison", "IN": "Indianapolis", "MI": "Lansing", "IL": "Springfield"}
)

In [ ]:
capitals + ", " + states

Even though the capitals were in a different order than the states, pandas match them up using the index. So the index seems to serve as a key for the rest of the data. However, pandas does not require that the index be unique!

In [ ]:
cities = pd.Series(
    ["Chicago", "Indianapolis", "Madison", "Lansing", "Springfield", "Milwaukee"],
    index=["IL", "IN", "WI", "MI", "IL", "WI"],
)

Thus, if we ask for the values associated with "IL", we get back not a single value but a series of values:

In [ ]:
cities["IL"]

and we get something more like a join when doing the concatenation now:

In [ ]:
cities + ", " + states

In the food inspections dataset, we might notice that the `inspection_id` column might be a unique identifier for each inspection. We can check this using the `is_unique` property.

In [ ]:
df.inspection_id.is_unique

Since it's unique, this is a good candidate for an index, and we can move it from a "normal" column to become the index using the `set_index` method.

In [ ]:
dfidx = df.set_index("inspection_id")

Now, instead of querying for a specific inspection using the `inspection_id`, we can use `.loc` to track it down. In many cases, this is not reason enough to worry about setting the index to a more meaningful value, but we will see where it can be more useful when transforming data.

In [ ]:
dfidx.loc[2498181]

### Group By

Another case where the index changes is when we group items. For some simple cases, we don't need the full `groupby` method. If we want to count the number of inspection results of each type, we can use the `value_counts` method directly on that column:

In [ ]:
dfidx.results.value_counts()

This returns a series with the result values as the labels and the counts as the values. We can achieve the same result, albeit unsorted, using groupby by using the `size()` method:

In [ ]:
dfidx.groupby("results").size()

##### Exercise

What if we want to count by both the `inspection_type` and `results`? Try out different methods to achieve this. What works and what doesn't?

##### Solution

In [ ]:
dfidx[["inspection_type", "results"]].value_counts()  # works

In [ ]:
dfidx.groupby("inspection_type", "results").size()  # does not work

In [ ]:
dfidx.groupby(["inspection_type", "results"]).size()  # works

#### Aggregations

Counting can help in some cases, but we might want to perform some statistics on the columns as well. This dataset doesn't have a lot of quantitative values, but the `inspection_date` is one that we can use. For example, we might compute the mean inspection date for a given zip code.

Some common aggregation functions are: 
- `size` (count of how many items are in the group)
- `sum`
- `min` and `max`
- `mean`
- `median`
- `std` (standard deviation)
- `var` (variance)

In [ ]:
dfidx.groupby("zip")["inspection_date"].mean()

This isn't all that useful on its own, however, because we don't know if those zip codes that seemingly aren't inspected often or are typos or devoid of food establishments. We'd like to have both the mean and the count. We can do this using the `agg` method and specifying the functions as strings:

In [ ]:
dfidx.groupby("zip").agg({"inspection_date": "mean", "results": "count"}).sort_values(
    "results", ascending=False
)

We could also include the maximum inspection date from this part of the dataset:

In [ ]:
dfidx.groupby("zip").agg({"inspection_date": ["mean", "max"], "results": "count"})

Note that the sort does not work here because we now have a multi-layered column header. We can use tuples to access the desired column:

In [ ]:
dfidx.groupby("zip").agg(
    {"inspection_date": ["mean", "max"], "results": "count"}
).sort_values(("results", "count"), ascending=False)

If we want to see all the values in a group, we can use the `list` constructor to accomplish this. Here, we also use an *expression* in the group by that extracts the year from the inspection date using the `dt` accessor.

In [ ]:
dfidx.query("license == 2517129").groupby(dfidx.inspection_date.dt.year).agg(
    {"results": list}
)

##### Exercise

For each year starting in 2019, find the number of facilities for each risk level that passed with conditions. Ignore those risk levels that do not start with the text `"Risk"`

In [ ]:
# Your code here

##### Solution

In [ ]:
dfidx[dfidx["risk"].fillna("").str.startswith("Risk")].groupby(
    [dfidx["inspection_date"].dt.year, "risk"]
).size().loc[2019:]

### String Processing

A key feature of pandas is its ability to apply python's string methods to entire columns. The method for doing this uses python's extensible accessors which serve to allow libraries to add their own "namespaces" to pandas objects. The `str` accessor is built-in and provides string methods for pandas. Many of these methods mimic existing methods of python string objects while others integrate functionality offered by regular expressions.

If we just search for locations named `"McDonald's"`, we find far fewer inspections than we would expect.

In [ ]:
dfidx[dfidx.dba_name == "McDonald's"]

Looking back at the dataset, you might notice that the names of establishments are generally in all caps. We can match against the captialized version by transforming all of the names to uppercase.

In [ ]:
dfidx[dfidx.dba_name.str.upper() == "MCDONALD'S"]

That's better but still seems like too few results over an almost four-year period. This might be because there are extra characters in the name (e.g. "McDonald's #11290" or "McDonald's Restaurant"). The `contains` method will allow McDonald's to appear anywhere and has a `case` flag that allows us to ignore casing.

In [ ]:
dfidx[dfidx.dba_name.fillna("").str.contains("mcdonald's", case=False)]

Now, we might wonder if there are some locations where the apostrophe is dropped (McDonalds). In this case, we could search for those specifically, but we could also create a **regular expression** that specifies the possibility--but not requirement--of an apostrophe. Learning regular expressions takes some time, but mastering them provides important tools for pattern matching. Even if you have used them, a reference for all of the special characters can be useful. Python provides the [Regular Expression HOWTO](https://docs.python.org/3/howto/regex.html) as a handy reference and tutorial. For us, `'?` indicates that there exist zero or one apostrophe between final 'd' and 's'.

In [ ]:
mcds = dfidx[dfidx.dba_name.fillna("").str.contains("mcdonald'?s", case=False)]

We can count how many times each version of the name is used using `value_counts`, but we can also look at the number of unique names using `nunique()`

In [ ]:
mcds["dba_name"].value_counts()

In [ ]:
mcds["dba_name"].nunique()

### Data Transformation

A key component of a failed inspection is understanding the types of violations that the inspector found. In our data, this is all packed into the `violations` column. Let's look at this string from the above inspection using the textwrap module to break up the long string.

In [ ]:
import textwrap

textwrap.wrap(dfidx.loc[2498181, "violations"])

##### Exercise

Try to determine what the format of the violations string is by looking at other examples. First, think about how you might find inspections that have violations and then look at a few of them to see if you can observe a pattern.

##### Solution

We can use a query to find inspections where the results was "Fail" or look for inspections where the violations column is not empty.

In [ ]:
dfidx.query('results == "Fail"').violations

In [ ]:
dfidx[dfidx.violations.notnull()].violations

In [ ]:
textwrap.wrap(dfidx.loc[2498190, "violations"])

After examining a few of these, we might notice that there seems to be a pattern where there are a numbered rules, where each is followed by a dash and then comments about how the rule was violated, and rules are separated by the `|` symbol.

#### More String Methods

With this in mind, we can use some string methods that expand a string to a list of strings. Recall that the `split` method does just that for a given delimiter.

In [ ]:
violations = dfidx.violations.fillna("").str.split("|")

Now each entry in our column is a (possibly empty) list of strings. If our goal is to analyze the types of violations, we might wish to separate the individual violations out into the violation number, the violation text, and the comments about the violation. The first step is to separate the violations. `split` provides the `expand` keyword argument which creates new columns for each of these, but we can also use the `explode` method to separate each violation into a new row. Note that the index is maintained in both operations.

In [ ]:
dfidx.violations.fillna("").str.split("|", expand=True)

In [ ]:
violations = dfidx.violations.fillna("").str.split("|").explode()

Now, our goal is to separate each of these into the three pieces of information:

1. violation number
2. violation text
3. comments

Let's start with the violation number. It is a number followed by a dot. we could potentially use that dot to split the string again. We'd only want to split **once** however so we would use the `n` parameter to limit the number of splits.

In [ ]:
violations[violations != ""].str.split(".", n=1)

##### Exercise

We can also use the str accessor with the subscript operator to extract just the first item and convert it to an integer.

In [ ]:
# Your code here

##### Solution

In [ ]:
violations[violations != ""].str.split(".", n=1).str[0].astype(int)

#### Back to Regular Expressions

Another string method that pandas has related to regular expressions is the `extract` method. We can use it to construct a pattern to extract the violation number.

In [ ]:
violations[violations != ""].str.extract(r"^\s*(\d+)\.")

This leads to the unfortunate column name of `0`. We can name the column using [named groups](https://docs.python.org/3/howto/regex.html#non-capturing-and-named-groups) in the regex:

In [ ]:
violations[violations != ""].str.extract(r"^\s*(?P<violation_num>\d+)\.")

### Final Exercises

1. All right, we've started attacking our problem but we haven't finished it. It's now up to you to extract all three columns (violation_num, violation_text, comments) for all of the violations. Be careful. A few violations have no comments.

2. Now, determine which violation is **most frequent**. But before you do that, note that the violation numbers changed at some point in the past. Read through the [metadata](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5/about_data) to learn more. So you will need to split the violations into two groups and find the most frequent one across both groups.